                                MEC-E5012 - Vehicle Mechatronics: Control       

# Exercise 2 (25 p)

## Python - Dynamic Turtlebot model, Longitudinal & Lateral control

At the end of this exercise, you have developed your own dynamic model of the TurtleBot and implemented both longitudinal and lateral controllers with the following tasks:

**Task 1: Dynamic Turtlebot model (5 p)**:
a model that is based on forces acting on the Turtlebot with vehicle speed as the output

**Task 2: Longitudinal PID controller (5 p)**:
a controller for the dynamic model to accurately set the speed for the vehicle

**Task 3: Lateral control: follow-the-carrot (7 p)**:
a steering controller, which is based on the error between the current heading and a heading that would direct to the target path

**Task 4: Lateral control: pure pursuit (8 p)**:
a geometric steering controller, which generates an arc to follow that leads to the target path


# Task 1: Dynamic Turtlebot model
In this task, you will create a turtlebot model that is based on system dynamics.
You can use the following equations as a reference while building your model.

\begin{align*}
\Sigma{F} &= F_x - F_d - F_r - mg\sin{\alpha} \\
\dot{v} &= \frac{\Sigma{F}}{m} \\
v_{k+1} &= v_k + \frac{\Sigma{F}}{m}\Delta t \\
v_{k+1} &= v_k + \frac{F_x - F_d - F_r - mg\sin{\alpha}}{m}\Delta t \\
\end{align*}

The model is a discrete time model and the controlled system variable in the longitudinal direction is the gas pedal, which is denoted as <code>gas</code>. The gas pedal has a range of 0-100 %, which translates to 0-2 Newtons of tractive force, $F_x$. The resistive forces are denoted as $F_d$ for the aerodynamic drag force and $F_r$ for the rolling resistance. The TurtleBot in reality can only go 0.22 m/s but for the sake of this exercise we will pretend that the max speed is 10 m/s for the drag force to have an effect. Note that the TurtleBot is operating on flat terrain the entire time.

First the required libraries are imported and the <code>DynamicTurtle</code>-class is initialized.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = [12, 8]

### Preliminary grader to give you a reference on how good is your solution ###
def grader(t,v,v_ref,n):
    mae = (1/n)*np.sum(np.abs(v-v_ref))
    passed = True
    if t == 1 and mae > 2:
        passed = False
    if t == 2 and mae > 0.2:
        passed = False
    if t == 3 and mae > 0.03:
        passed = False
    if t == 4 and mae > 0.02:
        passed = False
    return mae, passed
###############################################################################

class DynamicTurtle():
    def __init__(self):
        self.v = 0
        self.v_ref = 0
        
        self.g = 9.81 #Gravitational acceleration
        self.m = 1 # Weight (kg)
        self.rrc = 0.015 # Rolling resistance coefficient
        self.Cd = 0.5 # Coefficient of Drag
        self.A = 0.034 # Frontal Area
        self.roo = 1.22 # Density of Air

        self.Fr = 0
        self.Fd = 0
        self.Fx = 0
        self.Fx_max = 2

        # Controller parameters
        self.error = 0
        self.cumulative_error = 0
        self.change_in_error = 0
        self.previous_error = 0
        self.Kp = 0
        self.Ki = 0
        self.Kd = 0
        
        self.sample_time = 0.01
        
    def reset(self):
        self.v = 0
        self.v_ref = 0
        
        self.Fr = 0
        self.Fd = 0
        self.Fx = 0

Next, you will be continuing the defintion of the <code>DynamicTurtle</code>-class. Code a one step that the model takes. The logic behind the code should be
1. <code>gas</code> sets the tractive force
2. Calculate the resistive forces
3. **Update the velocity value of the model**

In [ ]:
class DynamicTurtle(DynamicTurtle):
    def step(self, gas):
        self.Fx = gas*self.Fx_max
        
        ### YOUR CODE HERE ~3 LINES ###

        
        
        ###
        
        pass

Now that you have a model to compute a discrete time step, it is time to test it. The code below is used to drive the Turtlebot for 20 seconds. The gas is set to 50 % for the entire time. The reference speed is the target, yet we notice that open loop control is not very accurate or reliable, since it falls short and with no feedback the system does not know that it is failing to meet the reference speed.

In [ ]:
model = DynamicTurtle()
time = 20

#Initialize data
t_data = np.arange(0,time,model.sample_time)
x_data = np.zeros_like(t_data)
v_data = np.zeros_like(t_data)

# Target
v_ref = np.zeros_like(t_data)
v_ref[0:1000] = np.arange(0,10,model.sample_time)
v_ref[1000:2000] = 10

gas = 0.5 # 50 %

for i in range(t_data.shape[0]):
    v_data[i] = model.v
    model.step(gas)

plt.plot(t_data, v_data, label='Actual')
plt.plot(t_data, v_ref, label='Reference')
plt.ylabel('Speed (v)')
plt.xlabel('Time(s)')
plt.grid()
plt.legend()
plt.show()

# Grading [THIS IS NOT AUTOMATIC GRADER, JUST TO ASSIST IN GRADING]
mae, passed = grader(1, v_data, v_ref, t_data.shape[0])
print('< --- Grading based on velocity accuracy --- >')
print('Your Turtlebot followed the target path within %.2f m/s mean absolute error' % (mae))
print()
if passed:
    print('Looking good, the error is quite low!')
else:
    print('Over 2 m/s mean absolute error. Improve your model to reduce the error.')

# Task 2: Longitudinal PID controller

Now that we have a model and open loop control, let's add PID controller and upgrade our system from open loop to closed loop feedback system. The following steps need to be taken:
1. Calculate the error
2. Calculate cumulative and change in the error
3. Set current error to <code>self.previous_error</code> for next loop
4. Set P, I, D values

In [ ]:
class DynamicTurtle(DynamicTurtle):
    def PID(self, v_ref):
        
        ### YOUR CODE HERE ~7 LINES ###

        #Note: check the given variables for PID errors in the initialization of DynamicTurtle -class.

        P = 0 # Zeros are here only as placeholders, replace them with your code
        I = 0
        D = 0
        ###
        
        gas = P+I+D
        return gas
    
    # Helper functions to tune the controller gains in the next cell
    
    def setKp(self, Kp):
        self.Kp = Kp
        
    def setKi(self, Ki):
        self.Ki = Ki
        
    def setKd(self, Kd):
        self.Kd = Kd


In [ ]:
model = DynamicTurtle()
model.reset()

#Initialize data
t_data = np.arange(0,time,model.sample_time)
x_data = np.zeros_like(t_data)
v_data = np.zeros_like(t_data)
gas = 0 # Initally no gas

# Set PID controller gains (use model.setK_() command where _ is p,i or d)
### YOUR CODE ~3 LINES ###



###

for i in range(t_data.shape[0]):
    v_data[i] = model.v
    gas = model.PID(v_ref[i])
    model.step(gas)

    
plt.plot(t_data, v_data, label='Actual')
plt.plot(t_data, v_ref, label='Reference')
plt.ylabel('Speed (v)')
plt.xlabel('Time(s)')
plt.grid()
plt.legend()
plt.show()

# Grading [THIS IS NOT AUTOMATIC GRADER, JUST TO ASSIST IN GRADING]
mae, passed = grader(2, v_data, v_ref, t_data.shape[0])
print('< --- Grading based on velocity accuracy --- >')
print('Your Turtlebot followed the target path within %.2f m/s mean absolute error' % (mae))
print()
if passed:
    print('Looking good, the error is quite low!')
else:
    print('Over 0.2 m/s mean absolute error. Improve your model to reduce the error.')

# Task 3: Follow-the-carrot
Here we introduce lateral control to the TurtleBot. We will utilize the <code>KinematicTurtle</code>-class developed in the exercise round 1.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import clear_output
%matplotlib inline

class KinematicTurtle():
    def __init__(self):
        self.w1 = 0 # Wheel 1 speed
        self.w2 = 0 # Wheel 2 speed
        self.x = 0 # X coordinate
        self.y = 0 # Y coordinate
        self.theta = 0 # Heading
        self.w = 0 # Angular speed
        self.v = 0 # Speed
        
        self.l = 0.16 # Wheelbase
        self.r = 0.033 # Wheel radius
        self.v_max = 0.22 # Maximum speed
        self.w_max = 2.84 # Maximum angular speed
        
        self.Kp = 0.7
        self.la = 0.3
        
        self.sample_time = 0.3
        
    def vw_step(self, v, w):
        self.x = self.x + v*np.cos(self.theta)*self.sample_time
        self.y = self.y + v*np.sin(self.theta)*self.sample_time
        
        self.w1 = ((2*v + w*self.l)/(2*self.r))
        self.w2 = ((2*v - w*self.l)/(2*self.r))
        self.theta = self.theta + (self.r*(self.w1 - self.w2)/self.l)*self.sample_time
        
    def reset(self):
        self.w1 = 0 # Wheel 1 speed
        self.w2 = 0 # Wheel 2 speed
        self.x = 0 # X coordinate
        self.y = 0 # Y coordinate
        self.theta = 0 # Heading
        self.w = 0 # Angular speed
        self.v = 0 # Speed

The third task is about implementing follow-the-carrot (FTC) control, which was presented in this week's lecture. Simply put, the controller looks ahead to a goal point in the future of the target path and tries to adjust the angle so that the current heading and the heading from the car to the goal point are the same. The controller gets its name from the reseblance of donkey following a carrot, its only purpose being to focus on the carrot and go that way.

The follow-the-carrot control is defined as the <code>ftc</code>-function. The following steps are required to implement the control:

1. Define the index of the closest point in the target path
2. Find the index of the goal point by travelling along the curve the distance of at least lookahead distance (<code>self.la</code>)
3. Define the goal point <code>xg, yg</code>
4. Calculate the angle error (difference between current heading and goal point)
5. define <code>steer</code> as the product of angle error and proportional gain (<code>self.Kp</code>)

In [ ]:
class KinematicTurtle(KinematicTurtle):
    def ftc(self, xt, yt):
        
        ### YOUR CODE HERE ~10 LINES ###
        
        
        ###
        
        # The goal point
        xg = 0.000001 # these values are here only as placeholders, replace them with your code
        yg = 0.000001
        
        # Angle between current heading and goal point
        alpha = np.arctan((yg-self.y)/(xg-self.x))
        # Angle error
        angle_error = alpha - self.theta
        steer = self.Kp * angle_error
        ###
        
        return steer, [self.x, xg], [self.y, yg]

In [ ]:
model = KinematicTurtle()
model.reset()
time = 20

t_data = np.arange(0,time,model.sample_time)
x_data = np.zeros_like(t_data)
y_data = np.zeros_like(t_data)

# Target path to follow
xt = np.linspace(0,3.5,num = t_data.shape[0])
yt = np.zeros_like(t_data)

model.y = 0.10 # starting offset

def live_plot(x, y, xl, yl, figsize=(7,5)):
    clear_output(wait=True)
    plt.figure(figsize=figsize)
    plt.scatter(x[-1], y[-1], s=150, alpha=0.5, label='Turtle')
    plt.plot(x, y, label= "Actual path")
    plt.plot(xt, yt, label="Target path")
    plt.plot(xl, yl, label="Look ahead")
    plt.grid(True)
    plt.xlabel('x (m)')
    plt.ylabel('y (m)')
    plt.legend()
    plt.show();

x = []
y = []
for i in range(t_data.shape[0]):
    # For grading
    x_data[i] = model.x
    y_data[i] = model.y
    [steer, xl, yl] = model.ftc(xt,yt)
    
    # For liveplotting
    x.append(model.x)
    y.append(model.y)
    live_plot(x, y, xl, yl)
    
    # For model updating
    model.vw_step(0.15, steer)

# Grading [THIS IS NOT AUTOMATIC GRADER, JUST TO ASSIST IN GRADING]
mae, passed = grader(3, y_data, yt, t_data.shape[0])
print('< --- Grading based on velocity accuracy --- >')
print('Your Turtlebot followed the target path within %.2f m mean absolute error' % (mae))
print()
if passed:
    print('Looking good, the error is quite low!')
else:
    print('Over 0.03 m mean absolute error. Improve your model to reduce the error.')

# Task 4: Pure pursuit

This is a tricky one. It gets its name for literally looking ahead at the target path trying to chase that point pure based on geometrical arc between the current location and the target point. The following steps are required to implement the control:

1. Define the index of the closest point in the target path
2. Find the index of the goal point by travelling along the curve the distance of at least lookahead distance (<code>self.la</code>)
3. Define the goal point <code>xg, yg</code>
4. Define the goal point in vehicle coordinates
5. Calculate the lenght of the lookahead line: <code>L</code>
6. Calculate the yl (refer to the lecture slide picture of the Pure pursuit)
7. Calculate the radius of the turning arc and take the inverse of it to get the steering command: <code>gamma</code>


In [ ]:
class KinematicTurtle(KinematicTurtle):
    def pure_pursuit(self, xt, yt):
        
        ### YOUR CODE HERE ~15 LINES ###

        

        # goal point in the target path
        x2 = 0 # Zeros are here only as placeholders, replace them with your code
        y2 = 0

        
        
        ###
        
        # Curvature of the arc (gamma) is the inverse of the radius (R). 
        # The concept of curvature provides a way to measure how sharply a smooth curve turns. 
        # A circle has constant curvature.
        # curvature is rate of change of rotation and will be used as the steering command.
        gamma = 0 # Zero is here only as a placeholder, replace it with your code
       
        
        return gamma, [self.x, x2], [self.y, y2]

In [ ]:
model = KinematicTurtle()
model.reset()
time = 20

t_data = np.arange(0,time,model.sample_time)
x_data = np.zeros_like(t_data)
y_data = np.zeros_like(t_data)

# Path to follow
xt = np.linspace(0,3.5,num = t_data.shape[0])
yt = np.zeros_like(t_data)

model.y = 0.10 # starting offset

def live_plot(x, y, xl, yl, figsize=(7,5)):
    clear_output(wait=True)
    plt.figure(figsize=figsize)
    plt.scatter(x[-1], y[-1], s=150, alpha=0.5, label='Turtle')
    plt.plot(x, y, label= "Actual path")
    plt.plot(xt, yt, label="Target path")
    plt.plot(xl, yl, label="Look ahead")
    plt.grid(True)
    plt.xlabel('x (m)')
    plt.ylabel('y (m)')
    plt.legend()
    plt.show();

x = []
y = []
# t_data.shape[0]
for i in range(t_data.shape[0]):
    # For grading
    x_data[i] = model.x
    y_data[i] = model.y
    [steer, xl, yl] = model.pure_pursuit(xt,yt)
    # For liveplotting
    x.append(model.x)
    y.append(model.y)
    live_plot(x, y, xl, yl)
    
    # For model updating
    model.vw_step(0.15, steer)

# Grading [THIS IS NOT AUTOMATIC GRADER, JUST TO ASSIST IN GRADING]
mae, passed = grader(4, y_data, yt, t_data.shape[0])
print('< --- Grading based on velocity accuracy --- >')
print('Your Turtlebot followed the target path within %.2f m mean absolute error' % (mae))
print()
if passed:
    print('Looking good, the error is quite low!')
else:
    print('Over 0.02 m mean absolute error. Improve your model to reduce the error.')

Congratulations for completing the exercise! :)

<b> Submit only this Jupyter Notebook file to MyCourses. </b>
